In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils
import torch.distributions
import numpy as np
import matplotlib.pyplot as plt
from  tqdm import tqdm
import os
import torch.optim as optim
import idx2numpy
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms
# Load the labels file
trainPath = "fashion-MNIST/train-images-idx3-ubyte"
testPath = "fashion-MNIST/t10k-images-idx3-ubyte"
label="fashion-MNIST/train-labels-idx1-ubyte"

In [2]:
train = idx2numpy.convert_from_file(trainPath)
test = idx2numpy.convert_from_file(testPath)
labels=idx2numpy.convert_from_file(label)
images_root_folder = "images-fashion-CNN-VAE"
if not os.path.exists(f"{images_root_folder}"):
    os.mkdir(f"{images_root_folder}")

device = 'cuda' if torch.cuda.is_available() else 'cpu'
PATH="VAE-CNN-Fashion_MNIST-Dataset-Model"
EPOCHS=75
lr=0.001
latent_dim=64
beta = 5
batch_size=100
# train=torch.utils.data.DataLoader(train,batch_size=batch_size,shuffle=True)

In [ ]:
class CustomDataset(Dataset):
    def __init__(self, images, labels, transform=None):
        self.images = images
        self.labels = labels
        self.transform = transform

    def __len__(self):
        return len(self.images)

    def __getitem__(self, idx):
        image = self.images[idx]
        label = self.labels[idx]
        
        if self.transform:
            image = self.transform(image)
        
        return image, label

# Assuming you have 'images' as a numpy array of your images and 'labels' as a numpy array of labels
transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Resize((28, 28)),  # Resize images to a specific size
    transforms.Normalize((0.5,), (0.5,)) 
])

train = CustomDataset(train, labels, transform=transform)
batch_size = 100
train = DataLoader(train, batch_size=batch_size, shuffle=False)

In [3]:
class Encoder(nn.Module):
    def __init__(self,x):
        super(Encoder, self).__init__()
        # First convolutional layer
        self.conv1 = nn.Conv2d(in_channels=1, out_channels=32, kernel_size=5, stride=1)
        self.relu1 = nn.ReLU()
        self.maxpool1 = nn.MaxPool2d(kernel_size=2, stride=2)

        # Second convolutional layer
        self.conv2 = nn.Conv2d(in_channels=32, out_channels=64, kernel_size=5, stride=1)
        self.relu2 = nn.ReLU()
        self.maxpool2 = nn.MaxPool2d(kernel_size=2, stride=2)

        # Fully connected layers
        self.flatten = nn.Flatten(start_dim=1)
        self.fc1 = nn.Linear(4 * 4 * 64, 4 * 4 * 64)  # Adjust the input and output sizes
        self.relu3 = nn.ReLU()
        self.fc2 = nn.Linear(4 * 4 * 64, x)  # Output size for 10 classes
        

        
        self.dis=torch.distributions.Normal(0, 1)
        self.dis.loc = self.dis.loc.cuda() # hack to get sampling on the GPU
        self.dis.scale = self.dis.scale.cuda()
        self.kld=0
        

    
    
    def forward(self, x):
        #print("Encode-------------")
        #print("Init : ",x.shape)

        x = self.conv1(x)
        #print("conv1 : ",x.shape)
        
        x = self.relu1(x)
        #print("relu1 : ",x.shape)
        
        x = self.maxpool1(x)
        #print("maxpool1  :",x.shape)
        
        x = self.conv2(x)
        #print("conv2 : ",x.shape)
        
        x = self.relu2(x)
        #print("relu2 : ",x.shape)
        
        x = self.maxpool2(x)
        #print("maxpool2 : ",x.shape)

        x = self.flatten(x)
        #print("flatten : ",x.shape)
        
        x = self.fc1(x)
        #print("fc1 : ",x.shape)
        
        x = self.relu3(x)
        #print("relu3 : ",x.shape)
        
        mu = self.fc2(x)
        
        #print("fc2 : ",x.shape)
        
        sig=torch.exp(self.fc2(x))
        z=mu + sig*self.dis.sample(mu.shape)
        self.kld=(sig**2 + mu**2 - torch.log(sig) - 1/2).sum()
        return z
    
    
    
        

class Decoder(nn.Module):
    def __init__(self,x):
        super(Decoder, self).__init__()
        
        self.fc1 = nn.Linear(x, 1024)
        self.relu1 = nn.ReLU()
        
        
        self.batchnorm1 = nn.BatchNorm1d(1024)
#         self.batchnorm1 = nn.LayerNorm(1024)
        
        
        self.fc2 = nn.Linear(1024, 7 * 7 * 128)
        self.relu2 = nn.ReLU()
        self.batchnorm2 = nn.BatchNorm1d(7 * 7 * 128)
#         self.batchnorm2 = nn.LayerNorm(7 * 7 * 128)
        

#         self.reshape =nn.view(batch_size, 128, 7, 7)  # Reshape into (batch_size, channels, height, width)

        self.conv_transpose1 = nn.ConvTranspose2d(128, 64, kernel_size=4, stride=2)
        self.relu3 = nn.ReLU()
        self.batchnorm3 = nn.BatchNorm2d(64)

        self.conv_transpose2 = nn.ConvTranspose2d(64, 1, kernel_size=13, stride=1)
        self.sigmoid = nn.Sigmoid()
        

    def forward(self, x):
        #print("\nDecode-------------")
        #print("Init : ",x.shape)
        
        x = self.fc1(x)
        #print("fc1 : ",x.shape)
        
        x = self.relu1(x)
        #print("relu1 : ",x.shape)
        
        
        x = self.batchnorm1(x)
        #print("batchnorm1 : ",x.shape)

        x = self.fc2(x)
        #print("fc2 : ",x.shape)
        
        x = self.relu2(x)
        #print("relu2 : ",x.shape)
        
        x = self.batchnorm2(x)
        #print("batchnorm2 : ",x.shape)
        
#         x = self.reshape(x)
        #print("reshape : ",x.shape)
        x=x.view(batch_size, 128, 7, 7)

        x = self.conv_transpose1(x)
        #print("conv_transpose1 : ",x.shape)
        
        x = self.relu3(x)
        #print("relu3 : ",x.shape)
        
        x = self.batchnorm3(x)
        #print("batchnorm3 : ",x.shape)
        
        x = self.conv_transpose2(x)
        #print("conv_transpose2 : ",x.shape)
        
#         x = self.sigmoid(x)
        #print("sigmoid : ",x.shape)
        
        return x


class Cifar100_VAE(nn.Module):
    def __init__(self,x):
        super(Cifar100_VAE, self).__init__()
        self.enc=Encoder(x)
        self.dec=Decoder(x)
        
    def forward(self,x):
        x =self.enc(x)        
        return self.dec(x)


def chaap2(orignal,decoded, idx, epo):
    if not os.path.exists(f"{images_root_folder}/{epo}"):
        os.mkdir(f"{images_root_folder}/{epo}")
    
    if not os.path.exists(f"{images_root_folder}/{epo}/{idx}"):
        os.mkdir(f"{images_root_folder}/{epo}/{idx}")
    
    org=torch.tensor(orignal)
    org=org.detach().cpu().numpy()
    dec=torch.tensor(decoded)
    dec=dec.detach().cpu().numpy()
    
    for i in range(0,org.shape[0]+1,20):
        if(i == org.shape[0]):
            i-=1
        org_i = np.resize(org[i],(28,28))
        dec_i = np.resize(dec[i],(28,28))
        #print(ogr_i.shape)
        
     
        if not os.path.exists(f"{images_root_folder}/{epo}/{idx}/{i}"):
            os.mkdir(f"{images_root_folder}/{epo}/{idx}/{i}")

        output_path = f"{images_root_folder}/{epo}/{idx}/{i}"
        plt.imsave(f"{output_path}/original.png" , org_i, cmap='gray')
        plt.imsave(f"{output_path}/decoded.png" , dec_i , cmap='gray') 

In [ ]:
vaenc=Cifar100_VAE(latent_dim).to(device)
opt = torch.optim.Adam(vaenc.parameters(),lr=lr)
for i in tqdm(range(EPOCHS)):
    for batch_idx,(x,_) in (enumerate(train)):
        
#         x=train[idx*batch_size:(idx+1)*(batch_size)]
            
#         x = x.reshape(batch_size,1,28,28)
        opt.zero_grad()
#         x=x/255

#         x = torch.from_numpy(x)
#         x=x.to(torch.float32)
        x = x.to(device) # GPU
        xx=vaenc.forward(x)

        if(batch_idx % 100 == 0 or batch_idx == 599):
            chaap2(x,xx, batch_idx, i)
#         x = x.reshape(28,28)
        losses = ((x - xx)**2).sum() +beta* vaenc.enc.kld

        #print(xx)
        
        losses.backward()
        opt.step()


torch.save(vaenc.state_dict(), PATH)

Test.......

In [ ]:
beta_6_model = Cifar100_VAE(latent_dim).to(device)
beta_6_model.load_state_dict(torch.load("VAE-CNN-Fashion_MNIST-Dataset-Model-Beta-6"))

In [ ]:
required = torch.randn(100,64);
plt.figure(figsize=(1,1))

plt.imshow(vaenc.dec(required.to(device)).detach().cpu().numpy().reshape(100,28,28)[0],cmap='gray')

required6 = torch.randn(100,64);
plt.figure(figsize=(1,1))

plt.imshow(beta_6_model.dec(required6.to(device)).detach().cpu().numpy().reshape(100,28,28)[0],cmap='gray')

In [4]:
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score

In [ ]:
train = idx2numpy.convert_from_file(trainPath)
test = idx2numpy.convert_from_file(testPath)
# train=torch.Tensor(train)
# test=torch.Tensor(test)
# train=torch.flatten(train,start_dim=1)
# test=torch.flatten(test,start_dim=1)
label="fashion-MNIST/train-labels-idx1-ubyte"
labels=idx2numpy.convert_from_file(label)
manik = Cifar100_VAE(latent_dim).to(device)
manik.load_state_dict(torch.load("VAE-CNN-Fashion_MNIST-Dataset-Model"))

In [ ]:
labels=labels.reshape(60000,-1)
train=train.reshape(60000,784)
train=np.hstack((train,labels))
print(train.shape)
X_train, X_test, y_train, y_test = train_test_split(train[:,:-1], train[:,-1], test_size=0.95, random_state=42,stratify=train[:,-1])

In [ ]:
lambda_function = lambda row:manik.enc(torch.tensor(row,dtype=torch.float32).to(device))
train2 =[lambda_function((row.reshape(1,1,28,28))) for row in (train[:,:-1])]



In [ ]:
for i in range(len(train2)):
    train2[i]=train2[i].detach().cpu().numpy()

In [ ]:
train2=np.array(train2).reshape(60000,64)
train2.shape

In [ ]:
train2=np.hstack((train2,labels))

In [ ]:
nan_rows = np.isnan(train2).any(axis=1)
train2 = train2[~nan_rows]

In [ ]:
 X_train1, X_test1, y_train1, y_test1 = train_test_split(train2[:,:-1], train2[:,-1], test_size=0.95, random_state=42,stratify=train2[:,-1])

In [ ]:
del train
del train2
del test
del labels

In [ ]:
print(X_train1[400])

In [ ]:
model1 = SVC(kernel='linear', C=1.0, decision_function_shape='ovr')  # You can adjust the kernel and parameters

# Train the model
model1.fit(X_train1, y_train1)

In [ ]:
y_pred1 = model1.predict(X_test1)

# Calculate accuracy



In [ ]:
accuracy = accuracy_score(y_test1, y_pred1)
print(f"Accuracy: {accuracy}")

In [5]:
class NormalizeKar(Dataset):
    def __init__(self, images, transform=None):
        self.images = images
        self.transform = transform

    def __len__(self):
        return len(self.images)

    def __getitem__(self, idx):
        image = self.images[idx]

        
        if self.transform:
            image = self.transform(image)
        
        return image, label

# Assuming you have 'images' as a numpy array of your images and 'labels' as a numpy array of labels
transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Resize((28, 28)),  # Resize images to a specific size
    transforms.Normalize((0.5,), (0.5,)) 
])

Ntrain = NormalizeKar(train, transform=transform)
trainNormalized = DataLoader(Ntrain, batch_size=1, shuffle=False)



In [6]:
manik = Cifar100_VAE(latent_dim).to(device)
manik.load_state_dict(torch.load("VAE-CNN-Fashion_MNIST-Dataset-Model"))

<All keys matched successfully>

In [7]:
for row in trainNormalized:
    print(row[0].shape)

C:\Users\Vaibhav Tanwar\AppData\Roaming\Python\Python310\site-packages\torchvision\transforms\functional.py:152: UserWarning: The given NumPy array is not writable, and PyTorch does not support non-writable tensors. This means writing to this tensor will result in undefined behavior. You may want to copy the array to protect its data or make it writable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at ..\torch\csrc\utils\tensor_numpy.cpp:212.)
  img = torch.from_numpy(pic.transpose((2, 0, 1))).contiguous()


torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
torch.Size([1, 1, 28, 28])
t

In [8]:
lambda_function = lambda row:manik.enc(row.to(device))
trainNormalized =[lambda_function(row[0]) for row in  (trainNormalized)]

In [9]:
for i in range(len(trainNormalized)):
    trainNormalized[i]=trainNormalized[i].detach().cpu().numpy()
trainNormalized=np.array(trainNormalized).reshape(60000,64)
trainNormalized.shape

(60000, 64)

In [10]:
labels = labels.reshape(60000, -1)

In [11]:
trainNormalized=np.hstack((trainNormalized,labels))

In [12]:
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score

In [13]:
 X_train1, X_test1, y_train1, y_test1 = train_test_split(trainNormalized[:,:-1], trainNormalized[:,-1], test_size=0.95, random_state=42,stratify=trainNormalized[:,-1])

In [ ]:
model1 = SVC(kernel='linear', C=1.0, decision_function_shape='ovr')  # You can adjust the kernel and parameters

# Train the model
model1.fit(X_train1, y_train1)

In [ ]:
y_pred1 = model1.predict(X_test1)

In [ ]:
accuracy = accuracy_score(y_test1, y_pred1)
print(f"Accuracy: {accuracy}")

In [ ]:
dummy_class=y_train1.max()+1
#list used for classifiers 
my_models=[]
for class_ in tqdm(np.unique(y_train1)):
    #select the index of our  class
    select=(y_train1==class_)
    temp_y=np.zeros(y_train1.shape)
    #class, we are trying to classify 
    temp_y[y_train1==class_]=class_
    #set other samples  to a dummy class 
    temp_y[y_train1!=class_]=dummy_class
    #Train model and add to list 
    model=SVC(kernel='linear', gamma=.5, probability=True)    
    my_models.append(model.fit(X_train1,temp_y))
     
    

In [ ]:
probability_array=np.zeros((X_test1.shape[0],11))
for j,model in enumerate(my_models):

    real_class=np.where(np.array(model.classes_)!=11)[0]

    probability_array[:,j]=model.predict_proba(X_test1)[:,real_class][:,0]

In [ ]:
one_vs_all=np.argmax(probability_array,axis=1)


In [ ]:
accuracy_score(y_test1,one_vs_all)

In [ ]:
X_train1.shape

In [ ]:
torch.save(manik.state_dict(), "manik-model")

In [ ]:
import numpy as np

# Example raw scores (replace this with your own data)
raw_scores = np.random.randn(5, 1024)

# Apply softmax along axis 1 to convert to probabilities across 1024 classes
def softmax(x):
    e_x = np.exp(x - np.max(x, axis=1, keepdims=True))
    return e_x / e_x.sum(axis=1, keepdims=True)

# Apply softmax to get probabilities across 10 classes
softmax_scores = softmax(raw_scores)

# Get probabilities for the first class (index 0) to the tenth class (index 9)
probabilities_for_10_classes = softmax_scores[:, :10]

print("Original Raw Scores:")
print(raw_scores)

print("\nSoftmax Applied (Probabilities for 10 Classes):")
print(probabilities_for_10_classes)


In [14]:
class Softmax(nn.Module):
    def __init__(self,x):
        super(Softmax, self).__init__()
        self.layer_64_1024 = nn.Linear(latent_dim, 1024)
        self.layer_1024_10 = nn.Linear(1024, 10)
    
    def forward(self,z):
        z = self.layer_64_1024(z)
        z = F.relu(z)
        z = self.layer_1024_10(z)
        return z

def getEncodedData(train):
    encoded_train = []
    for x in tqdm(train):
        x=x/255
        x=x.to(torch.float32)
        x = x.to(device) # GPU
        xx=manik.enc.forward(x)
        encoded_train.append(xx)
    return encoded_train

# manik-vae = Cifar100_VAE(latent_dim).to(device)
# manik.load_state_dict(torch.load("CNN-VAE-Fashion_MNIST-Dataset-Model"))

In [16]:
num_epochs=100
softmanik = Softmax(64).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(softmanik.parameters(), lr=0.001)
y_train1 = np.array(y_train1,dtype=np.int32)
for epoch in tqdm(range(100)):
    for i,x in enumerate(X_train1):
        x = torch.tensor(x,dtype=torch.float32).to(device)
        
        optimizer.zero_grad()
        outputs = softmanik.forward(x)
        loss = criterion(outputs, torch.tensor(y_train1[i],dtype=torch.long).to(device))
        loss.backward()
        if (epoch + 1) % 2 == 0:
            print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}')
        optimizer.step()

  1%|▊                                                                                 | 1/100 [00:05<09:02,  5.48s/it]

Epoch [2/100], Loss: 0.1083
Epoch [2/100], Loss: 1.2041
Epoch [2/100], Loss: 0.7076
Epoch [2/100], Loss: 1.2071
Epoch [2/100], Loss: 2.8918
Epoch [2/100], Loss: 0.0681
Epoch [2/100], Loss: 0.5817
Epoch [2/100], Loss: 0.2496
Epoch [2/100], Loss: 8.2130
Epoch [2/100], Loss: 1.6446
Epoch [2/100], Loss: 0.2400
Epoch [2/100], Loss: 0.0441
Epoch [2/100], Loss: 0.4001
Epoch [2/100], Loss: 1.5926
Epoch [2/100], Loss: 0.9999
Epoch [2/100], Loss: 0.1577
Epoch [2/100], Loss: 1.1151
Epoch [2/100], Loss: 0.5690
Epoch [2/100], Loss: 1.2688
Epoch [2/100], Loss: 4.3134
Epoch [2/100], Loss: 0.2051
Epoch [2/100], Loss: 1.1128
Epoch [2/100], Loss: 0.7095
Epoch [2/100], Loss: 1.7469
Epoch [2/100], Loss: 0.5457
Epoch [2/100], Loss: 0.6017
Epoch [2/100], Loss: 0.3528
Epoch [2/100], Loss: 0.4227
Epoch [2/100], Loss: 1.5608
Epoch [2/100], Loss: 0.0863
Epoch [2/100], Loss: 2.0609
Epoch [2/100], Loss: 2.1979
Epoch [2/100], Loss: 0.7652
Epoch [2/100], Loss: 3.4713
Epoch [2/100], Loss: 1.8832
Epoch [2/100], Loss:

  2%|█▋                                                                                | 2/100 [00:11<09:12,  5.63s/it]

Epoch [2/100], Loss: 1.3568
Epoch [2/100], Loss: 0.7851
Epoch [2/100], Loss: 0.3570
Epoch [2/100], Loss: 0.4463
Epoch [2/100], Loss: 2.3895
Epoch [2/100], Loss: 0.1437
Epoch [2/100], Loss: 1.5807
Epoch [2/100], Loss: 0.1001
Epoch [2/100], Loss: 1.8050
Epoch [2/100], Loss: 0.0028
Epoch [2/100], Loss: 0.4764
Epoch [2/100], Loss: 0.5195
Epoch [2/100], Loss: 2.2780
Epoch [2/100], Loss: 1.0460
Epoch [2/100], Loss: 0.6398
Epoch [2/100], Loss: 0.4669
Epoch [2/100], Loss: 0.9776
Epoch [2/100], Loss: 1.9615
Epoch [2/100], Loss: 3.4594
Epoch [2/100], Loss: 0.1824
Epoch [2/100], Loss: 1.8241
Epoch [2/100], Loss: 1.6964
Epoch [2/100], Loss: 0.1241
Epoch [2/100], Loss: 0.3500
Epoch [2/100], Loss: 2.8295
Epoch [2/100], Loss: 0.3144
Epoch [2/100], Loss: 1.0909
Epoch [2/100], Loss: 1.4504
Epoch [2/100], Loss: 0.4462
Epoch [2/100], Loss: 0.7499
Epoch [2/100], Loss: 0.7559
Epoch [2/100], Loss: 0.0359
Epoch [2/100], Loss: 1.3234
Epoch [2/100], Loss: 0.0795
Epoch [2/100], Loss: 1.1274
Epoch [2/100], Loss:

  3%|██▍                                                                               | 3/100 [00:16<08:54,  5.51s/it]

...

Epoch [98/100], Loss: 0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: 0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: 0.0097
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: 0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100], Loss: -0.0000
Epoch [98/100]

 99%|████████████████████████████████████████████████████████████████████████████████▏| 99/100 [09:04<00:05,  5.39s/it]

Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: 0.0008
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: 0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: 0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/

100%|████████████████████████████████████████████████████████████████████████████████| 100/100 [09:10<00:00,  5.51s/it]

Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: 0.0004
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: 0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: 0.0003
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: -0.0000
Epoch [100/100], Loss: 0.0000
Epoch [100/100], Loss: 0.0000
Epoch [100/10

In [17]:
PATH="maniksoftCNN"
torch.save(softmanik.state_dict(), PATH)

In [21]:
for i,x in enumerate(y_test1):
    if(i%2):
        ans[i]=x

In [24]:
ans=[]
for i,x in enumerate(X_test1):
    input_tensor=softmanik(torch.tensor(x).to(device))
    y=torch.argmax(F.softmax(input_tensor, dim=0))
    ans.append(y.item()!=y_test1[i])



sum(ans)/len(ans)

0.8298187121
